# Optuna Hyperparameter Tuning in DoubleML

## Comparing Tuned vs. Untuned Models

This notebook demonstrates the impact of hyperparameter tuning using Optuna on the performance of Double Machine Learning models. We'll run a simulation study to compare:

1. **Untuned Model**: Using default hyperparameters
2. **Grid Search Tuning**: Traditional exhaustive grid search
3. **Optuna (TPE)**: Bayesian optimization with Tree-structured Parzen Estimator
4. **Optuna (GP)**: Bayesian optimization with Gaussian Process sampler
5. **Optuna (Random)**: Random search baseline

We'll evaluate both statistical performance (bias, RMSE, coverage) and computational efficiency.

This notebook uses parallel processing with `joblib` to run multiple simulations simultaneously, allowing us to run more simulation repetitions in less time.

In [28]:
# Import required libraries
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import time
from tqdm.notebook import tqdm
from joblib import Parallel, delayed

import doubleml as dml
from doubleml import DoubleMLData
from doubleml.plm.datasets import make_plr_CCDDHNR2018

from sklearn.ensemble import RandomForestRegressor
from sklearn.tree import DecisionTreeRegressor

import warnings
import optuna

warnings.filterwarnings("ignore")
sns.set_style("whitegrid")
plt.rcParams["figure.figsize"] = (12, 6)
optuna.logging.set_verbosity(optuna.logging.WARNING)
np.random.seed(42)

## Data Generating Process

We use the data generating process from Chernozhukov et al. (2018) which implements a Partially Linear Regression (PLR) model where:
- $\theta_0 = 0.5$ is the true treatment effect (our target parameter)

In [2]:
# Configuration for simulation
N_SIM = 50  # Number of simulation runs (increased thanks to parallelization!)
N_OBS = 500  # Sample size per simulation
N_VARS = 50  # Number of covariates
TRUE_THETA = 0.5  # True treatment effect
N_JOBS = 8  # Number of parallel jobs (-1 = use all CPU cores)

print(f"Simulation Configuration:")
print(f"  • Sample size: {N_OBS}")
print(f"  • Number of covariates: {N_VARS}")
print(f"  • Simulation runs: {N_SIM}")
print(f"  • True treatment effect θ₀: {TRUE_THETA}")
print(f"  • Parallel jobs: {N_JOBS} (all available cores)")

Simulation Configuration:
  • Sample size: 500
  • Number of covariates: 50
  • Simulation runs: 50
  • True treatment effect θ₀: 0.5
  • Parallel jobs: 8 (all available cores)


In [27]:
# Check available CPU cores
import multiprocessing

n_cores = multiprocessing.cpu_count()
print(f"\nSystem Information:")
print(f"  • Available CPU cores: {n_cores}")
print(f"  • Will use: {n_cores if N_JOBS == -1 else N_JOBS} cores for parallel processing")


System Information:
  • Available CPU cores: 16
  • Will use: 8 cores for parallel processing


## Setup: Define Tuning Strategies

In [26]:
# Define parameter grids for tuning
# Note: Reduced grid for faster computation - grid search is exhaustive!
param_grid_rf = {
    "ml_l": {
        "n_estimators": [100, 200, 500],  # Reduced from 5 to 3 options
        "max_depth": [5, 10, 20],  # Reduced from 5 to 3 options
        "min_samples_leaf": [1, 10, 20],  # Reduced from 4 to 3 options
        "max_features": ["sqrt", 0.5],  # Reduced from 3 to 2 options
    },
    "ml_m": {
        "n_estimators": [100, 200, 500],
        "max_depth": [5, 10, 20],
        "min_samples_leaf": [1, 10, 20],
        "max_features": ["sqrt", 0.5],
    },
}

# Optuna settings with different samplers
optuna_settings_tpe = {
    "n_trials": 30,
    "sampler": optuna.samplers.TPESampler(seed=42),
    "show_progress_bar": False,
    "verbosity": optuna.logging.WARNING,
}

optuna_settings_gp = {
    "n_trials": 30,
    "sampler": optuna.samplers.GPSampler(seed=42),
    "show_progress_bar": False,
    "verbosity": optuna.logging.WARNING,
}

optuna_settings_random = {
    "n_trials": 30,
    "sampler": optuna.samplers.RandomSampler(seed=42),
    "show_progress_bar": False,
    "verbosity": optuna.logging.WARNING,
}

print("Parameter Grid:")
grid_combinations = (
    len(param_grid_rf["ml_l"]["n_estimators"])
    * len(param_grid_rf["ml_l"]["max_depth"])
    * len(param_grid_rf["ml_l"]["min_samples_leaf"])
    * len(param_grid_rf["ml_l"]["max_features"])
)
print(f"  • Grid search combinations per learner: {grid_combinations}")
print(f"  • Total grid evaluations (2 learners): {2 * grid_combinations}")
print(f"  Grid search evaluates ALL {2 * grid_combinations} combinations (exhaustive search)")
print(f"\nOptuna Configurations:")
print(f"  • Number of trials per learner: 30")
print(f"  • Samplers: TPE, Gaussian Process, Random")
print(f"  • Total Optuna evaluations per sampler (2 learners): {2 * 30}")
print(f"\n Optuna evaluates only ~{100 * 30 / grid_combinations:.0f}% of the parameter space")

Parameter Grid:
  • Grid search combinations per learner: 54
  • Total grid evaluations (2 learners): 108
  Grid search evaluates ALL 108 combinations (exhaustive search)

Optuna Configurations:
  • Number of trials per learner: 30
  • Samplers: TPE, Gaussian Process, Random
  • Total Optuna evaluations per sampler (2 learners): 60

 Optuna evaluates only ~56% of the parameter space


## Simulation Study

We'll compare five approaches:
1. **No tuning**: Default Random Forest parameters
2. **Grid search**: Exhaustive search over parameter grid
3. **Optuna (TPE)**: Bayesian optimization with Tree-structured Parzen Estimator
4. **Optuna (GP)**: Bayesian optimization with Gaussian Process sampler
5. **Optuna (Random)**: Random search baseline for Optuna

In [5]:
def run_single_simulation(seed, method="no_tuning", optuna_settings=None):
    """
    Run a single simulation iteration.

    Parameters
    ----------
    seed : int
        Random seed for reproducibility
    method : str
        One of 'no_tuning', 'grid_search', 'optuna_tpe', 'optuna_gp', 'optuna_random'
    optuna_settings : dict, optional
        Optuna settings dictionary

    Returns
    -------
    dict : Results containing estimate, std error, CI, and time
    """
    # Generate data
    np.random.seed(seed)
    data = make_plr_CCDDHNR2018(n_obs=N_OBS, dim_x=N_VARS, theta=TRUE_THETA, return_type="DataFrame")

    # Prepare DoubleML data
    x_cols = [col for col in data.columns if col.startswith("X")]
    dml_data = DoubleMLData(data, "y", "d", x_cols)

    # Initialize learners
    ml_l = RandomForestRegressor(random_state=seed, n_jobs=1)
    ml_m = RandomForestRegressor(random_state=seed, n_jobs=1)

    # Initialize model
    dml_plr = dml.DoubleMLPLR(dml_data, ml_l, ml_m, n_folds=2, score="partialling out")

    start_time = time.time()

    # Apply tuning strategy
    if method == "grid_search":
        dml_plr.tune(param_grids=param_grid_rf, search_mode="grid_search", n_folds_tune=3, set_as_params=True)
    elif method.startswith("optuna"):
        dml_plr.tune(
            param_grids=param_grid_rf,
            search_mode="optuna",
            optuna_settings=optuna_settings,
            n_folds_tune=3,
            set_as_params=True,
        )
    # else: no_tuning - use defaults

    # Fit the model
    dml_plr.fit()

    elapsed_time = time.time() - start_time

    # Extract results
    coef = dml_plr.coef[0]
    se = dml_plr.se[0]
    ci_lower = dml_plr.confint().values[0, 0]
    ci_upper = dml_plr.confint().values[0, 1]

    return {
        "estimate": coef,
        "se": se,
        "ci_lower": ci_lower,
        "ci_upper": ci_upper,
        "time": elapsed_time,
        "coverage": ci_lower <= TRUE_THETA <= ci_upper,
    }


print("🎬 Starting simulation study...")
print("This may take a few minutes...\n")

🎬 Starting simulation study...
This may take a few minutes...



In [6]:
# Run simulations for each method (with parallelization and progress bar)
results = {"no_tuning": [], "grid_search": [], "optuna_tpe": [], "optuna_gp": [], "optuna_random": []}

methods_config = [
    ("no_tuning", None, "No Tuning"),
    ("grid_search", None, "Grid Search"),
    ("optuna_tpe", optuna_settings_tpe, "Optuna (TPE Sampler)"),
    ("optuna_gp", optuna_settings_gp, "Optuna (GP Sampler)"),
    ("optuna_random", optuna_settings_random, "Optuna (Random Sampler)"),
]

print(f"🚀 Running {N_SIM} simulations per method with parallel processing...")
print(f"   Using {N_JOBS} parallel jobs (all available cores)\n")

for method, settings, display_name in methods_config:
    print(f"\n{'='*60}")
    print(f"  Running {display_name}")
    print(f"{'='*60}")

    start_time = time.time()

    # Run simulations in parallel with progress bar
    method_results = Parallel(n_jobs=N_JOBS, verbose=0)(
        delayed(run_single_simulation)(seed=1000 + i, method=method, optuna_settings=settings)
        for i in tqdm(range(N_SIM), desc=f"  Progress", leave=False)
    )

    results[method] = method_results
    elapsed = time.time() - start_time

    print(f"  ✓ Completed {N_SIM} simulations in {elapsed:.1f} seconds ({elapsed/N_SIM:.2f}s per simulation)")

print("\n✅ All simulations complete!")

🚀 Running 50 simulations per method with parallel processing...
   Using 8 parallel jobs (all available cores)


  Running No Tuning


  Progress:   0%|          | 0/50 [00:00<?, ?it/s]

  ✓ Completed 50 simulations in 28.4 seconds (0.57s per simulation)

  Running Grid Search


  Progress:   0%|          | 0/50 [00:00<?, ?it/s]

  ✓ Completed 50 simulations in 2030.0 seconds (40.60s per simulation)

  Running Optuna (TPE Sampler)


...

  ✓ Completed 50 simulations in 571.8 seconds (11.44s per simulation)

  Running Optuna (GP Sampler)


  Progress:   0%|          | 0/50 [00:00<?, ?it/s]

  ✓ Completed 50 simulations in 577.3 seconds (11.55s per simulation)

  Running Optuna (Random Sampler)


  Progress:   0%|          | 0/50 [00:00<?, ?it/s]

  ✓ Completed 50 simulations in 389.9 seconds (7.80s per simulation)

✅ All simulations complete!


## Analyze Results

Let's compute key performance metrics:
- **Bias**: How far estimates are from the truth on average
- **RMSE**: Root mean squared error (combines bias and variance)
- **Coverage**: Proportion of confidence intervals containing true value
- **Computation Time**: Wall-clock time for tuning + fitting

In [22]:
# Convert results to DataFrame
results_df = pd.DataFrame([{"method": method, **result} for method in results.keys() for result in results[method]])

# Compute summary statistics
summary_stats = []
for method in ["no_tuning", "grid_search", "optuna_tpe", "optuna_gp", "optuna_random"]:
    method_results = results_df[results_df["method"] == method]

    bias = np.mean(method_results["estimate"]) - TRUE_THETA
    rmse = np.sqrt(np.mean((method_results["estimate"] - TRUE_THETA) ** 2))
    coverage = np.mean(method_results["coverage"])
    mean_time = np.mean(method_results["time"])

    # Pretty names for display
    method_names = {
        "no_tuning": "No Tuning",
        "grid_search": "Grid Search",
        "optuna_tpe": "Optuna (TPE)",
        "optuna_gp": "Optuna (GP)",
        "optuna_random": "Optuna (Random)",
    }

    summary_stats.append(
        {"Method": method_names[method], "Bias": bias, "RMSE": rmse, "Coverage (95% CI)": coverage, "Avg. Time (s)": mean_time}
    )

summary_df = pd.DataFrame(summary_stats)

# Display results
print("\n" + "=" * 70)
print("=" * 70)
print(f"\nTrue treatment effect: θ₀ = {TRUE_THETA}")
print(f"Number of simulations: {N_SIM}\n")

# Format the table nicely
display_df = summary_df.copy()
display_df["Bias"] = display_df["Bias"].apply(lambda x: f"{x:+.4f}")
display_df["RMSE"] = display_df["RMSE"].apply(lambda x: f"{x:.4f}")
display_df["Coverage (95% CI)"] = display_df["Coverage (95% CI)"].apply(lambda x: f"{x:.2%}")
display_df["Avg. Time (s)"] = display_df["Avg. Time (s)"].apply(lambda x: f"{x:.2f}")

print(display_df.to_string(index=False))
print("\n" + "=" * 70)



True treatment effect: θ₀ = 0.5
Number of simulations: 50

         Method    Bias   RMSE Coverage (95% CI) Avg. Time (s)
      No Tuning -0.0139 0.0531            92.00%          3.56
    Grid Search +0.0098 0.0456            96.00%        303.50
   Optuna (TPE) +0.0066 0.0457            98.00%         84.24
    Optuna (GP) +0.0066 0.0457            98.00%         86.90
Optuna (Random) +0.0066 0.0457            98.00%         57.97



In [21]:
fig, axes = plt.subplots(2, 3, figsize=(18, 10))
axes = axes.flatten()

methods = ["no_tuning", "grid_search", "optuna_tpe", "optuna_gp", "optuna_random"]
colors = ["#FF6B6B", "#4ECDC4", "#45B7D1", "#96CEB4", "#FFEAA7"]
titles = ["No Tuning (Defaults)", "Grid Search", "Optuna (TPE)", "Optuna (GP)", "Optuna (Random)"]

for idx, (method, color, title) in enumerate(zip(methods, colors, titles)):
    ax = axes[idx]
    method_data = results_df[results_df["method"] == method]

    # KDE plot (better for small sample sizes)
    sns.kdeplot(data=method_data["estimate"], ax=ax, color=color, fill=True, alpha=0.5, linewidth=2.5, label="Distribution")

    # True value line
    ax.axvline(TRUE_THETA, color="red", linestyle="--", linewidth=2, label=f"True θ = {TRUE_THETA}")

    # Mean estimate line
    mean_est = method_data["estimate"].mean()
    ax.axvline(mean_est, color="darkgreen", linestyle="-", linewidth=2, label=f"Mean = {mean_est:.3f}")

    ax.set_xlabel("Estimated Treatment Effect", fontsize=11)
    ax.set_ylabel("Density", fontsize=11)
    ax.set_title(title, fontsize=13, fontweight="bold")
    ax.legend(fontsize=9)
    ax.grid(True, alpha=0.3)

# Hide the extra subplot
axes[5].axis("off")

plt.tight_layout()
plt.savefig("optuna_simulation_distributions.png", dpi=300, bbox_inches="tight")
plt.show()

In [20]:
fig, axes = plt.subplots(2, 2, figsize=(14, 10))

methods_display = ["No Tuning", "Grid Search", "Optuna (TPE)", "Optuna (GP)", "Optuna (Random)"]
colors = ["#FF6B6B", "#4ECDC4", "#45B7D1", "#96CEB4", "#FFEAA7"]

# 1. Bias Comparison
ax = axes[0, 0]
biases = [summary_df[summary_df["Method"] == m]["Bias"].values[0] for m in methods_display]
bars = ax.bar(range(len(methods_display)), np.abs(biases), color=colors, edgecolor="black", linewidth=1.5)
ax.set_xticks(range(len(methods_display)))
ax.set_xticklabels(methods_display, rotation=45, ha="right", fontsize=9)
ax.set_ylabel("Absolute Bias", fontsize=11, fontweight="bold")
ax.set_title("Bias (Lower is Better)", fontsize=12, fontweight="bold")
ax.grid(axis="y", alpha=0.3)
for i, bar in enumerate(bars):
    height = bar.get_height()
    ax.text(
        bar.get_x() + bar.get_width() / 2.0,
        height,
        f"{biases[i]:+.4f}",
        ha="center",
        va="bottom",
        fontsize=9,
        fontweight="bold",
    )

# 2. RMSE Comparison
ax = axes[0, 1]
rmses = [summary_df[summary_df["Method"] == m]["RMSE"].values[0] for m in methods_display]
bars = ax.bar(range(len(methods_display)), rmses, color=colors, edgecolor="black", linewidth=1.5)
ax.set_xticks(range(len(methods_display)))
ax.set_xticklabels(methods_display, rotation=45, ha="right", fontsize=9)
ax.set_ylabel("RMSE", fontsize=11, fontweight="bold")
ax.set_title("Root Mean Squared Error (Lower is Better)", fontsize=12, fontweight="bold")
ax.grid(axis="y", alpha=0.3)
for i, bar in enumerate(bars):
    height = bar.get_height()
    ax.text(
        bar.get_x() + bar.get_width() / 2.0, height, f"{rmses[i]:.4f}", ha="center", va="bottom", fontsize=9, fontweight="bold"
    )

# 3. Coverage Comparison
ax = axes[1, 0]
coverages = [summary_df[summary_df["Method"] == m]["Coverage (95% CI)"].values[0] for m in methods_display]
bars = ax.bar(range(len(methods_display)), coverages, color=colors, edgecolor="black", linewidth=1.5)
ax.axhline(0.95, color="red", linestyle="--", linewidth=2, label="Nominal 95%")
ax.set_xticks(range(len(methods_display)))
ax.set_xticklabels(methods_display, rotation=45, ha="right", fontsize=9)
ax.set_ylabel("Coverage Rate", fontsize=11, fontweight="bold")
ax.set_title("95% CI Coverage (Target: 0.95)", fontsize=12, fontweight="bold")
ax.set_ylim([0.8, 1.0])
ax.legend(fontsize=10)
ax.grid(axis="y", alpha=0.3)
for i, bar in enumerate(bars):
    height = bar.get_height()
    ax.text(
        bar.get_x() + bar.get_width() / 2.0,
        height,
        f"{coverages[i]:.1%}",
        ha="center",
        va="bottom",
        fontsize=9,
        fontweight="bold",
    )

# 4. Computation Time Comparison
ax = axes[1, 1]
times = [summary_df[summary_df["Method"] == m]["Avg. Time (s)"].values[0] for m in methods_display]
bars = ax.bar(range(len(methods_display)), times, color=colors, edgecolor="black", linewidth=1.5)
ax.set_xticks(range(len(methods_display)))
ax.set_xticklabels(methods_display, rotation=45, ha="right", fontsize=9)
ax.set_ylabel("Average Time (seconds)", fontsize=11, fontweight="bold")
ax.set_title("Computation Time", fontsize=12, fontweight="bold")
ax.grid(axis="y", alpha=0.3)
for i, bar in enumerate(bars):
    height = bar.get_height()
    ax.text(
        bar.get_x() + bar.get_width() / 2.0,
        height,
        f"{times[i]:.2f}s",
        ha="center",
        va="bottom",
        fontsize=9,
        fontweight="bold",
    )

plt.tight_layout()
plt.show()